In [1]:
# Parameters
country_name = "Zimbabwe"


# Optimization Problem Time Series

This notebook optimizes an electrci mix based on : 
- an electricity demand time serie
- a PV production time serie
- a wind production time serie

In [1]:
import numpy as np
import pandas as pd
from scipy.optimize import minimize
from pulp import *
import sys
from utilities import import_excel, optimize_enr_chu, format_load_data
import plotly.graph_objects as go
import plotly.express as px
import pickle
from ren_ninja_api import fetch_and_average_data_ren_ninja, get_regular_coordinates
import plotly.io as pio
import os
import glob
import geopandas as gpd
import matplotlib.pyplot as plt
pio.renderers.default='notebook'

Enter country name for file naming: 

In [2]:
year = 2021
country_name = 'Russia'
state_name = 'ALT'
country_name = country_name
state_name = state_name
# Directory path
path_input_data = '../input_time_series/'
mode = 'grid'
regions_match = pd.read_excel('match_plexos_iso_codes.xlsx')

regions_match = regions_match[regions_match['Country']==country_name].set_index('region')
plexos_region = regions_match.loc[state_name, 'plexos']
chu_plexos_match = pd.read_excel('../../../DATA/Chu et Hawkes/match_chu_plexos.xlsx', index_col=0)

region_chu = chu_plexos_match[chu_plexos_match['Plexos']==plexos_region].iloc[0, 0]
print(region_chu)
country_codes = pd.read_csv('../countries_codes_and_coordinates_adapted.csv' , sep = ',', index_col = 0)
country_code = country_codes.loc[country_name,'Alpha-3 code'].split( ' ')[1]

SI


In [3]:
# for code in chu_plexos_match.index:
#     if len(chu_plexos_match.loc[code,'Plexos'])==3:
#         chu_plexos_match.loc[code, 'iso_alpha3']= code.split('.')[0]
#         chu_plexos_match.loc[code,'Plexos']=''
#     else: 
#         chu_plexos_match.loc[code, 'iso_alpha3']= code.split('.')[0]
        
# chu_plexos_match.to_excel('../../../DATA/Chu et Hawkes/match_chu_plexos.xlsx')

# Extraction des données

### 1. Part des différentes classes de CF dans les zones 

FAIT : Normalement pas besoin de runner ces cellules !!!

In [4]:
zones_def = pd.read_excel('../../../DATA/Chu et Hawkes/2.Zone definition.xlsx', sheet_name='Zone')
zones_codes = zones_def['Zone Code']

In [5]:
zones_codes.to_list()

['AFG.East',
 'AFG.Northeast',
 'AFG.Northwest',
 'AFG.South',
 'AFG.West',
 'ALB.All',
 'DZA.Central',
 'DZA.North',
 'DZA.NorthEast',
 'DZA.NorthWest',
 'DZA.Sahara',
 'AGO.NorthEast',
 'AGO.NorthWest',
 'AGO.SouthEast',
 'AGO.SouthWest',
 'ARG.Central',
 'ARG.Comahue',
 'ARG.Cuyo',
 'ARG.NorthEast',
 'ARG.NorthWest',
 'ARG.Pampas',
 'ARG.PampasNorth',
 'ARG.Patagonia',
 'ARM.All',
 'AUS.NSW',
 'AUS.NT',
 'AUS.QLD',
 'AUS.SA',
 'AUS.TAS',
 'AUS.VIC',
 'AUS.WA',
 'AUT.East',
 'AUT.South',
 'AUT.West',
 'AZE.North',
 'AZE.South',
 'AZE.West',
 'BHR.All',
 'BGD.Barisal',
 'BGD.Chittagong',
 'BGD.Dhaka',
 'BGD.Khulna',
 'BGD.Rajshahi',
 'BGD.Rangpur',
 'BGD.Sylhet',
 'BLR.Brest',
 'BLR.Gomel',
 'BLR.Grodno',
 'BLR.Minsk',
 'BLR.Mogilev',
 'BLR.Vitebsk',
 'BEL.Flanders',
 'BEL.Wallonia',
 'BLZ.All',
 'BEN.All',
 'BTN.All',
 'BOL.Altiplano1',
 'BOL.Altiplano2',
 'BOL.SubAndean1',
 'BOL.SubAndean2',
 'BOL.Tropical',
 'BIH.All',
 'BWA.North',
 'BWA.South',
 'BRA.Region1',
 'BRA.Region10',
 '

In [6]:
wind_onshore_main = pd.read_excel('../../../DATA/Chu et Hawkes/6.Potential summary.xlsx', sheet_name='OnshoreWind_Zone_main')
wind_onshore_class =  pd.read_excel('../../../DATA/Chu et Hawkes/6.Potential summary.xlsx', sheet_name='OnshoreWind_Zone_class')

In [7]:
df = wind_onshore_class[wind_onshore_class['Zone']=='AFG.East']['Capacity Potential']

In [8]:
weight_class_wind_onshore = pd.DataFrame(index = zones_codes)
for i in range(1,11):
            # print(i)
            # print(j)
            weight_class_wind_onshore[f'class {i}']=np.zeros(len(weight_class_wind_onshore))

In [9]:
for zone in zones_codes:
    zone_capacity = wind_onshore_main[wind_onshore_main['Zone']==zone]['Capacity Potential'].values[0]
    j=12

    if zone_capacity !=0:
        for i in range(2,11):
            # print(i)
            # print(j)
            capacity_class = wind_onshore_class[wind_onshore_class['Zone']==zone][f'Unnamed: {j}'].values[0]

            weight_class_wind_onshore.loc[zone,f'class {i}'] = capacity_class/zone_capacity
            # print(capacity_class)
            # print(weight_class_wind_onshore.loc[zone,f'class {i}'])
            j+=1
        capacity_class = wind_onshore_class[wind_onshore_class['Zone']==zone]['Capacity Potential'].values[0]
        weight_class_wind_onshore.loc[zone,f'class 1'] = capacity_class/zone_capacity
    else : 
        for i in range(1,11):
            weight_class_wind_onshore.loc[zone,f'class {i}'] = 0

weight_class_wind_onshore.to_excel('../../../DATA/Chu et Hawkes/WindOnshore_weight_class_zones.xlsx') 

In [10]:
fixed_pv_main = pd.read_excel('../../../DATA/Chu et Hawkes/6.Potential summary.xlsx', sheet_name='FixedPV_Zone_main')
fixed_pv_class =  pd.read_excel('../../../DATA/Chu et Hawkes/6.Potential summary.xlsx', sheet_name='FixedPV_Zone_class')
weight_class_fixed_pv = pd.DataFrame(index = zones_codes)
for i in range(1,11):
            # print(i)
            # print(j)
            weight_class_fixed_pv[f'class {i}']=np.zeros(len(weight_class_fixed_pv))

In [11]:
fixed_pv_class

Zone     Area Unnamed: 2 Unnamed: 3 Unnamed: 4 Unnamed: 5  \
0             Unit      km2        NaN        NaN        NaN        NaN   
1          tranche  class 1    class 2    class 3    class 4    class 5   
2               CF    < 0.1  0.10-0.13  0.13-0.16  0.16-0.19  0.19-0.22   
3         AFG.East        0          0          0        534      14741   
4    AFG.Northeast        0          0         11       6639       1097   
..             ...      ...        ...        ...        ...        ...   
729      ZAF.WCape        0          0          0       3965      38712   
730       ZMB.East        0          0          0         12      15925   
731       ZMB.West        0          0          0          0      34760   
732       ZWE.East        0          0          0         69      16962   
733       ZWE.West        0          0          0       3850      33297   

    Unnamed: 6 Unnamed: 7 Capacity potential Unnamed: 9  ... Unnamed: 19  \
0          NaN        NaN                 MW        NaN  ...         NaN   
1      class 6    class 7            class 1    class 2  ...     class 5   
2    0.22-0.25     > 0.25              < 0.1  0.10-0.13  ...   0.19-0.22   
3         4465          0                  0          0  ...      0.2107   
4            0          0                  0          0  ...      0.2019   
..         ...        ...                ...        ...  ...         ...   
729        725          0                  0          0  ...      0.2086   
730          0          0                  0          0  ...      0.2053   
731          0          0                  0          0  ...      0.2083   
732          0          0                  0          0  ...       0.207   
733          0          0                  0          0  ...      0.2066   

    Unnamed: 20 Unnamed: 21 technical potential Unnamed: 23 Unnamed: 24  \
0           NaN         NaN               TWh/y         NaN         NaN   
1       class 6     class 7             class 1     class 2     class 3   
2     0.22-0.25      > 0.25               < 0.1   0.10-0.13   0.13-0.16   
3        0.2218         NaN                 NaN         NaN         NaN   
4           NaN         NaN                 NaN         NaN    0.469494   
..          ...         ...                 ...         ...         ...   
729      0.2215         NaN                 NaN         NaN    0.005592   
730         NaN         NaN                 NaN         NaN         NaN   
731         NaN         NaN                 NaN         NaN         NaN   
732         NaN         NaN                 NaN         NaN         NaN   
733         NaN         NaN                 NaN         NaN         NaN   

    Unnamed: 25  Unnamed: 26 Unnamed: 27 Unnamed: 28  
0           NaN          NaN         NaN         NaN  
1       class 4      class 5     class 6     class 7  
2     0.16-0.19    0.19-0.22   0.22-0.25      > 0.25  
3      26.22607   816.260211  260.279993         NaN  
4    310.407584    58.181313         NaN         NaN  
..          ...          ...         ...         ...  
729  186.204192  2122.191282   42.223739         NaN  
730    0.600193   859.206171         NaN         NaN  
731         NaN  1902.816451         NaN         NaN  
732    3.360091   922.745962         NaN         NaN  
733  189.791851   1807.84873         NaN         NaN  

[734 rows x 29 columns]

In [7]:
for zone in zones_codes:
    zone_capacity = fixed_pv_main[fixed_pv_main['Zone']==zone]['Capacity Potential'].values[0]
    j=9

    if zone_capacity !=0:
        for i in range(2,8):
            # print(i)
            # print(j)
            capacity_class = fixed_pv_class[fixed_pv_class['Zone']==zone][f'Unnamed: {j}'].values[0]

            weight_class_fixed_pv.loc[zone,f'class {i}'] = capacity_class/zone_capacity
            print(capacity_class)
            print(weight_class_fixed_pv.loc[zone,f'class {i}'])
            j+=1
        capacity_class = fixed_pv_class[fixed_pv_class['Zone']==zone]['Capacity potential'].values[0]
        weight_class_fixed_pv.loc[zone,f'class 1'] = capacity_class/zone_capacity
    else : 
        for i in range(1,11):
            weight_class_fixed_pv.loc[zone,f'class {i}'] = 0

weight_class_fixed_pv.to_excel('../../../DATA/Chu et Hawkes/FixedPV_weight_class_zones.xlsx')  

0
0.0
0
0.0
16027
0.027062166830736083
442242
0.7467415476108059
133960
0.22619628555845797
0
0.0
0
0.0
344
0.0014800600629025526
199183
0.856984893921858
32896
0.14153504601523945
0
0.0
0
0.0
0
0.0
0
0.0
477414
0.7705893366734243
142130
0.22941066332657567
0
0.0
0
0.0
0
0.0
0
0.0
0
0.0
1626690
0.9107792537913442
159352
0.08922074620865579
0
0.0
0
0.0
0
0.0
146859
0.1103597273676854
1170678
0.8797261653378221
13193
0.009914107294492496
0
0.0
0
0.0
12753
0.37900086183839043
20896
0.6209991381616096
0
0.0
0
0.0
0
0.0
0
0.0
0
0.0
70657
0.023010190241063634
3000026
0.9769898097589363
0
0.0
0
0.0
0
0.0
0
0.0
137515
0.8786564093389391
18991
0.12134359066106092
0
0.0
0
0.0
0
0.0
17
3.1463244452752386e-05
112762
0.20869755123419204
427534
0.7912709855213552
0
0.0
0
0.0
0
0.0
0
0.0
194380
0.3573253723441412
349606
0.6426746276558588
0
0.0
0
0.0
0
0.0
0
0.0
147
1.0665140560022902e-05
12567829
0.9118208355056604
1215246
0.08816849935377954
0
0.0
0
0.0
328
0.0008141503298798135
212291
0.5269414258

### 2. Génération des TS de CF par zone et techno

On récupère les séries temporelles de CF pour les différentes classes de CF et on applique à chacune les poids précédemments calculés pour obtenir une unique série temporelle par zone. 

In [10]:
for zone in zones_codes[:]:
    if not os.path.exists(f'../../../DATA/Chu et Hawkes/Wind_Onshore/{zone}/{zone}_wind_onshore_aggregated.xlsx'):
        wind_onshore_ts = pd.DataFrame()
        for year in range(2008,2018):
            wind_onshore_ts[year]=np.zeros(8760)
        weight_class_wind_onshore = pd.read_excel('../../../DATA/Chu et Hawkes/WindOnshore_weight_class_zones.xlsx', index_col = 0).loc[zone]
        for nclass in weight_class_wind_onshore.index:
            i = nclass.split(' ')[1]
            for year in range(2008,2018):
                try : 
                    ts = weight_class_wind_onshore.loc[nclass]*pd.read_csv(f'../../../DATA/Chu et Hawkes/Wind_Onshore/{zone}/class{i}.csv')[f'{year}.0']
                    wind_onshore_ts[year]+=ts
                except :
                    pass
        wind_onshore_ts.to_excel(f'../../../DATA/Chu et Hawkes/Wind_Onshore/{zone}/{zone}_wind_onshore_aggregated.xlsx', index = False)


In [11]:
# shapefile_path = './shapefiles/geoBoundariesCGAZ_ADM1.shp'
# gdf = gpd.read_file(shapefile_path)

# # Read the shapefile using Geopandas
# gdf = gpd.read_file(shapefile_path)
# # Optionally simplify the geometries to speed up plotting
# gdf['geometry'] = gdf['geometry'].simplify(tolerance=0.01)

# # Plot the shapefile with optimized parameters
# fig, ax = plt.subplots(figsize=(10, 10))
# gdf.plot(ax=ax, linewidth=0.5, edgecolor='k')

# # Show the plot
# plt.show()

In [13]:
for zone in zones_codes:
    if not os.path.exists(f'../../../DATA/Chu et Hawkes/PV_Fixed/{zone}/{zone}_pv_fixed_aggregated.xlsx'):
        pv_fixed_ts = pd.DataFrame()
        for year in range(2008,2018):
            pv_fixed_ts[year]=np.zeros(8760)
        weight_class_pv_fixed = pd.read_excel('../../../DATA/Chu et Hawkes/FixedPV_weight_class_zones.xlsx', index_col = 0).loc[zone]
        for nclass in weight_class_pv_fixed.index:
            i = nclass.split(' ')[1]
            for year in range(2008,2018):
                try : 
                    ts = weight_class_pv_fixed.loc[nclass]*pd.read_csv(f'../../../DATA/Chu et Hawkes/PV_Fixed/{zone}/class{i}.csv')[f'{year}.0']
                    pv_fixed_ts[year]+=ts
                except :
                    pass
        pv_fixed_ts.to_excel(f'../../../DATA/Chu et Hawkes/PV_Fixed/{zone}/{zone}_pv_fixed_aggregated.xlsx', index = False)

### 3. Load time series

# Optimisation

In [12]:
print(country_name)
print(state_name)

Russia
ALT


### Load Time Series

First we load the time series that will be used in the problem. We use the  ```import_excel``` function used in the wavelet decomposition.

#### Demand

In [13]:
# Demand time serie

dpd = 24 # data per day in the time serie
dpy = 365 # data per year :  cut the leap years to 365 years

ndpd = 24 # new data per day for hourly data (for the interpolation)
signal_length = ndpd * dpy
region_name = regions_match.loc[state_name, 'plexos']
file_name = format_load_data(country_name, state_name = region_name)
Load_ts = import_excel(path_input_data,file_name, 
                                    dpd ,ndpd, dpy, 
                                    interp=True, norm = 'mean') # interpolate data from dpd to ndpd numper of points per day
print(Load_ts)
# Répéter la série temporelle 10 fois
serie_temporelle_rep = np.tile(Load_ts, 10)

# Créer un DataFrame à partir de la série temporelle répétée
Load_ts = serie_temporelle_rep
mean_load = pd.read_excel(path_input_data+file_name).mean().iloc[0]

[1.18614888 1.17002805 1.13475864 ... 1.20161505 1.20812066 1.20198329]


In [14]:
len(Load_ts)

87600

#### Wind production

In [15]:
# Wind time serie 

dpd = 24 # data per day
dpy = 365 # data per year :  cut the leap years to 365 years

# We interpolate so that we have hourly data
ndpd = 24 # new data per day for hourly data (for the interpolation)
signal_length = ndpd * dpy

path_input_data = '../input_time_series/'
if state_name: 
    file_name = f'{country_name}/{country_code}_{region_chu}_wind_onshore_10y.xlsx'
    if not os.path.exists(path_input_data+f'{country_name}/{country_code}_{region_chu}_wind_onshore_10y.xlsx'):  
        print('here')
        file_name = f'{country_name}/{country_code}_{region_chu}_chu_wind_onshore_averaged.xlsx'
        df = pd.read_excel(path_input_data+file_name, index_col=0)
        
        time_series = pd.concat([df[col] for col in df.columns], ignore_index=True)
        result_df = pd.DataFrame({'Time Series': time_series})

        # Sauvegarder le résultat dans un nouveau fichier Excel
        result_df.to_excel(path_input_data+f'{country_name}/{country_code}_{region_chu}_wind_onshore_10y.xlsx', index=False)
        file_name = f'{country_name}/{country_code}_{region_chu}_wind_onshore_10y.xlsx'
else:
    file_name = f'{country_name}/{country_code}_full_wind_onshore_10y.xlsx'
    if not os.path.exists(path_input_data+f'{country_name}/{country_code}_full_wind_onshore_10y.xlsx'):
        file_name = f'{country_name}/{country_code}_full_chu_wind_onshore_averaged.xlsx'
        df = pd.read_excel(path_input_data+file_name, index_col=0)

        time_series = pd.concat([df[col] for col in df.columns], ignore_index=True)
        result_df = pd.DataFrame({'Time Series': time_series})

        # Sauvegarder le résultat dans un nouveau fichier Excel
        result_df.to_excel(path_input_data+f'{country_name}/{country_code}_full_wind_onshore_10y.xlsx', index=False)
        file_name = f'{country_name}/{country_code}_full_wind_onshore_10y.xlsx'
Wind_ts = import_excel(path_input_data,file_name, 
                                dpd ,ndpd, dpy, 
                                interp=True, norm = None) # interpolate data from dpd to ndpd numper of points per day

mean_wind = pd.read_excel(path_input_data+file_name).mean().iloc[0]

#### PV production

In [16]:
# PV time serie 

dpd = 24 # data per day
dpy = 365 # data per year :  cut the leap years to 365 years

# We interpolate so that we have hourly data
ndpd = 24 # new data per day for hourly data (for the interpolation)
signal_length = ndpd * dpy

path_input_data = '../input_time_series/'
if state_name: 
    file_name = f'{country_name}/{country_code}_{region_chu}_pv_fixed_10y.xlsx'
    if not os.path.exists(path_input_data+file_name):  
        file_name = f'{country_name}/{country_code}_{region_chu}_pv_fixed_aggregated.xlsx'
        df = pd.read_excel(path_input_data+file_name, index_col=0)

        time_series = pd.concat([df[col] for col in df.columns], ignore_index=True)
        result_df = pd.DataFrame({'Time Series': time_series})

        # Sauvegarder le résultat dans un nouveau fichier Excel
        result_df.to_excel(path_input_data+f'{country_name}/{country_code}_{region_chu}_pv_fixed_10y.xlsx', index=False)
        file_name = f'{country_name}/{country_code}_{region_chu}_pv_fixed_10y.xlsx'
else:
    file_name =f'{country_name}/{country_code}_full_pv_fixed_10y.xlsx'
    if not os.path.exists(path_input_data+file_name):
        file_name = f'{country_name}/{country_code}_full_chu_pv_fixed_averaged.xlsx'
        df = pd.read_excel(path_input_data+file_name, index_col=0)

        time_series = pd.concat([df[col] for col in df.columns], ignore_index=True)
        result_df = pd.DataFrame({'Time Series': time_series})

        # Sauvegarder le résultat dans un nouveau fichier Excel
        result_df.to_excel(path_input_data+f'{country_name}/{country_code}_full_pv_fixed_10y.xlsx', index=False)
        
PV_ts = import_excel(path_input_data,file_name, 
                                dpd ,ndpd, dpy, 
                                interp=True, norm = None) # interpolate data from dpd to ndpd numper of points per day

mean_pv = pd.read_excel(path_input_data+file_name).mean().iloc[0]

### Plot Time Series

In [17]:
# colors_dict = {
#     'Wind': 'steelblue',        
#     'PV': 'gold',
#     'Discharge': 'orangered',    
#     'SOC': 'darkgreen',           
#     'Charge': 'purple',
#     'Consumption': 'green',          
#     'Dispatchable': 'crimson',       
#     'Curtailment': 'cyan'    
# }

In [18]:
# Create a Plotly figure
fig = go.Figure()

fig.add_trace(go.Scatter(y=PV_ts, mode='lines', name='PV',marker=dict(color=colors_dict['PV'])))
fig.add_trace(go.Scatter(y=Load_ts, mode='lines', name='Demand',marker=dict(color=colors_dict['Consumption'])))
fig.add_trace(go.Scatter(y=Wind_ts, mode='lines', name='Wind',marker=dict(color=colors_dict['Wind'])))
fig.update_layout(title=f'{country_name} {state_name} 2021', xaxis_title='Hour', yaxis_title='Power normalized')

# Show the plot
fig.show()

### Description of the problem

#### Equations:

- **Objective function** : 
  - Minimize dispatchable energy: $ \min(\sum{P_{dispatchable}(t)*dt}) $


- **Node Law** : 
  - $(P_{pv}(t) + P_{wind}(t) + P_{dispatchable}(t) - P_{in\_stock}(t) + P_{out\_stock}(t) = P_{demand}(t) + P_{curt}(t))$


- **State of charge**
  - $SOC(t+1)=SOC(t)+P_{in\_stock}(t) - P_{out\_stock}(t)$

#### Contraintes :
- $E_{wind} + E_{pv} \leq E_{demand}$
- We want a maximum storage size of 10 hours:  $E_{stock} \leq 10$
- Charging and discharging at the same time is not possible. 


### Implementation
#### Decision Variables:
- `x_pv`: Installed capacity for photovoltaic production.
- `x_wind`: Installed capacity for wind production.
- `ts_dispatchable`: Dispatchable production (can be controlled), time serie.
- `p_ch`: Battery charging power, time serie.
- `p_dech`: Battery discharging power, time serie.
- `SOC_ts`: State of charge of the battery, time serie.
- `p_curt`: Curtailment power (lost energy), time serie.
- `dech_active`: Binary variable indicating if the battery is charging or discharging.

### Run the optimization with GUROBI

**If the optimization has already been run, go to the next part where results can be loaded and analysed in plots.**

In [21]:
optimized_parameters=optimize_enr_chu(country_name, Load_ts[:43800], PV_ts[:43800], Wind_ts[:43800], mean_load, state_name = state_name,save_results = True)

Gurobi Optimizer version 11.0.1 build v11.0.1rc0 (win64 - Windows 10.0 (19045.2))

CPU model: 11th Gen Intel(R) Core(TM) i5-1145G7 @ 2.60GHz, instruction set [SSE2|AVX|AVX2|AVX512]
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Academic license 2503220 - for non-commercial use only - registered to du___@ethz.ch
Optimize a model with 175201 rows, 262801 columns and 600037 nonzeros
Model fingerprint: 0xbe097517
Variable types: 219002 continuous, 43799 integer (0 binary)
Coefficient statistics:
  Matrix range     [1e-05, 1e+05]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+05]
  RHS range        [8e-01, 1e+05]
Found heuristic solution: objective 43800.735268
Presolve removed 4 rows and 43804 columns
Presolve time: 3.33s
Presolved: 175197 rows, 218997 columns, 531995 nonzeros
Found heuristic solution: objective 43800.730910
Variable types: 175198 continuous, 43799 integer (43799 binary)
Deterministic concurrent LP optimizer: primal simplex, d

### Add results to .csv file with all countries

In [ ]:
df_new = pd.DataFrame({"Country" : [country_name],"State":[state_name],"iso_alpha":[optimized_parameters['iso_alpha']],
    "mean_load":[optimized_parameters['mean_consumption']],
    "E_dispatch": [optimized_parameters['E_dispatch']],
    "P_dispatch": [optimized_parameters['dispatchable_capacity']],
    "E_destock": [optimized_parameters['E_destock']],
    "P_pv": [optimized_parameters['pv_capacity']],
    "P_wind": [optimized_parameters['wind_capacity']]
})


In [ ]:
all_results_file = "results/optimization_results_world_grid_with_states.csv"
file_exists = os.path.isfile(all_results_file)

df_new.to_csv(all_results_file, mode='a', index=False, header=not file_exists)

print(f"Data have been added to {all_results_file}")    

Data have been added to results/optimization_results_world_grid_with_states.csv


# Get DATA and format it 

In [7]:
for country_name in ['Australia', 'Brazil', 'Canada', 'China','Russia']: 
    country_code = country_codes.loc[country_name,'Alpha-3 code'].split( ' ')[1]
    print(country_code)
    regions_chu = chu_plexos_match[chu_plexos_match['iso_alpha3']==country_code]
    list_plexos_region = regions_chu['Plexos'].drop_duplicates().to_list()
    columns = ['2008', '2009', '2010', '2011', '2012', '2013', '2014','2015', '2016', '2017']
    for region in list_plexos_region:
        if not os.path.exists(f'../input_time_series/{country_name}/{country_code}_{region}_chu_wind_onshore_averaged.xlsx'):
            zone_chu = regions_chu[regions_chu['Plexos']==region]
            wind_ts = pd.DataFrame(0, index=np.arange(8760), columns=columns)
            for zone in zone_chu.index :
                wind_to_add = pd.read_excel(f'../../../DATA/Chu et Hawkes/Wind_Onshore/{zone}/{zone}_wind_onshore_aggregated.xlsx')
                wind_to_add.columns = wind_to_add.columns.astype(str)
                
                wind_ts += wind_to_add[columns]
            wind_ts=wind_ts/len(zone_chu)
            wind_ts.to_excel(f'../input_time_series/{country_name}/{country_code}_{region}_chu_wind_onshore_averaged.xlsx')

AUS
BRA
CAN
CHN
RUS


In [8]:
for country_name in country_codes.index[:]:
    country_code = country_codes.loc[country_name,'Alpha-3 code'].split( ' ')[1]
    if not os.path.exists(f'../input_time_series/{country_name}/{country_code}_full_chu_wind_onshore_averaged.xlsx'):
        try :
            print(country_code)
            regions_chu = chu_plexos_match[chu_plexos_match['iso_alpha3']==country_code]
            list_plexos_region = regions_chu['Plexos'].drop_duplicates().to_list()
            columns = ['2008', '2009', '2010', '2011', '2012', '2013', '2014','2015', '2016', '2017']
            wind_ts = pd.DataFrame(0, index=np.arange(8760), columns=columns)
            # print(regions_chu)
            for zone in regions_chu.index :
                wind_to_add = pd.read_excel(f'../../../DATA/Chu et Hawkes/Wind_Onshore/{zone}/{zone}_wind_onshore_aggregated.xlsx')
                wind_to_add.columns = wind_to_add.columns.astype(str)
                wind_ts += wind_to_add[columns]
            wind_ts=wind_ts/len(regions_chu)
            wind_ts.to_excel(f'../input_time_series/{country_name}/{country_code}_full_chu_wind_onshore_averaged.xlsx')
        except:
            pass

MDA
MNG
MNE
ESH
YEM
ZMB
ZWE


In [12]:
for country_name in ['Australia', 'Brazil', 'Canada', 'China', 'Russia']: 
    country_code = country_codes.loc[country_name,'Alpha-3 code'].split( ' ')[1]
    print(country_code)
    regions_chu = chu_plexos_match[chu_plexos_match['iso_alpha3']==country_code]
    list_plexos_region = regions_chu['Plexos'].drop_duplicates().to_list()
    columns = ['2008', '2009', '2010', '2011', '2012', '2013', '2014','2015', '2016', '2017']
    for region in list_plexos_region:
        if not os.path.exists(f'../input_time_series/{country_name}/{country_code}_{region}_pv_fixed_aggregated.xlsx'):
            zone_chu = regions_chu[regions_chu['Plexos']==region]
            pv_ts = pd.DataFrame(0, index=np.arange(8760), columns=columns)
            for zone in zone_chu.index :
                pv_to_add = pd.read_excel(f'../../../DATA/Chu et Hawkes/PV_Fixed/{zone}/{zone}_pv_fixed_aggregated.xlsx')
                pv_to_add.columns = pv_to_add.columns.astype(str)
                
                pv_ts += pv_to_add[columns]
            pv_ts=pv_ts/len(zone_chu)
            pv_ts.to_excel(f'../input_time_series/{country_name}/{country_code}_{region}_pv_fixed_aggregated.xlsx')

AUS
BRA
CAN
CHN
RUS


In [14]:
for country_name in country_codes.index[:]:
    country_code = country_codes.loc[country_name,'Alpha-3 code'].split( ' ')[1]
    if not os.path.exists(f'../input_time_series/{country_name}/{country_code}_full_chu_pv_fixed_averaged.xlsx'):
        try :
            print(country_code)
            regions_chu = chu_plexos_match[chu_plexos_match['iso_alpha3']==country_code]
            list_plexos_region = regions_chu['Plexos'].drop_duplicates().to_list()
            columns = ['2008', '2009', '2010', '2011', '2012', '2013', '2014','2015', '2016', '2017']
            pv_ts = pd.DataFrame(0, index=np.arange(8760), columns=columns)
            # print(regions_chu)
            for zone in regions_chu.index :
                pv_to_add = pd.read_excel(f'../../../DATA/Chu et Hawkes/PV_Fixed/{zone}/{zone}_pv_fixed_aggregated.xlsx')
                pv_to_add.columns = pv_to_add.columns.astype(str)
                pv_ts += pv_to_add[columns]
            pv_ts=pv_ts/len(regions_chu)
            pv_ts.to_excel(f'../input_time_series/{country_name}/{country_code}_full_chu_pv_fixed_averaged.xlsx')
        except:
            pass

AFG
ALB
DZA
AGO
ATA
ARG
ARM
AUS
AUT
AZE
BHR
BGD
BLR
BEL
BLZ
BEN
BTN
BOL
BIH
BWA
BRA
BRN
BGR
BFA
BDI
KHM
CMR
CAN
CPV
CAF
TCD
CHL
CHN
COL
COG
COD
CRI
CIV
HRV
CUB
CYP
CZE
DNK
DJI
DOM
ECU
EGY
SLV
GNQ
ERI
EST
ETH
FJI
FIN
FRA
GUF
GAB
GMB
GEO
DEU
GHA
GRC
GTM
GIN
GNB
GUY
HTI
HND
HUN
ISL
IND
IDN
IRN
IRQ
IRL
ISR
ITA
JAM
JPN
JOR
KAZ
KEN
PRK
KOR
KWT
KGZ
LAO
LVA
LBN
LSO
LBR
LBY
LTU
LUX
MKD
MDG
MWI
MYS
MLI
MLT
MRT
MUS
MEX
MDA
MNG
MNE
MAR
MOZ
MMR
NAM
NPL
NLD
NZL
NIC
NER
NGA
NOR
OMN
PAK
PAN
PNG
PRY
PER
PHL
POL
PRT
QAT
ROU
RUS
RWA
SAU
SEN
SRB
SLE
SGP
SVK
SVN
SOM
ZAF
ESP
LKA
SDN
SUR
SWZ
SWE
CHE
SYR
TWN
TJK
TZA
THA
TLS
TGO
TTO
TUN
TUR
TKM
UGA
UKR
ARE
GBR
USA
URY
UZB
VEN
VNM
ESH
YEM
ZMB
ZWE


## Plots

In [13]:
# from plots import plot_ts_optim, plot_pie_energy, plot_storage, plot_stack_production

In [14]:
# plot_ts_optim([optimized_parameters['optimized_pv'], optimized_parameters['optimized_wind'], optimized_parameters['optimized_dispatchable'], optimized_parameters['optimized_p_curt'],np.array(Load_ts) ], ['PV', 'Wind', 'Dispatchable', 'Curtailment', 'Consumption'], country_name, colors_dict = colors_dict,savefig=False)

In [15]:
# plot_storage(optimized_parameters['optimized_charge'], optimized_parameters['optimized_discharge'], optimized_parameters['optimized_stock'], country_name, colors_dict = colors_dict, savefig=False)

In [16]:
# E_wind = optimized_parameters['E_wind']
# E_pv = optimized_parameters['E_pv']
# E_dispatch = optimized_parameters['E_dispatch']

In [17]:
# plot_pie_energy([E_wind, E_pv, E_dispatch], country_name, colors_dict =colors_dict, savefig=False)